In [1]:
import pandas as pd
import numpy as np

In [2]:
corona_df = pd.read_csv(r'C:\Users\Lavish Singhal\Documents\Covid=19\covid-19-dataset-1.csv')
corona_df


FIPS      Admin2  Province_State      Country_Region  \
0     45001.0   Abbeville  South Carolina                  US   
1     22001.0      Acadia       Louisiana                  US   
2     51001.0    Accomack        Virginia                  US   
3     16001.0         Ada           Idaho                  US   
4     19001.0       Adair            Iowa                  US   
...       ...         ...             ...                 ...   
2619      NaN         NaN             NaN             Vietnam   
2620      NaN         NaN             NaN  West Bank and Gaza   
2621      NaN         NaN             NaN              Zambia   
2622      NaN         NaN             NaN            Zimbabwe   
2623      NaN  unassigned         Wyoming                  US   

              Last_Update        Lat       Long_  Confirmed  Deaths  \
0     2020-04-03 22:46:37  34.223334  -82.461707          6       0   
1     2020-04-03 22:46:37  30.295065  -92.414197         72       1   
2     2020-04-03 22:46:37  37.767072  -75.632346          8       0   
3     2020-04-03 22:46:37  43.452658 -116.241552        307       3   
4     2020-04-03 22:46:37  41.330756  -94.471059          1       0   
...                   ...        ...         ...        ...     ...   
2619  2020-04-03 22:46:20  14.058324  108.277199        237       0   
2620  2020-04-03 22:46:20  31.952200   35.233200        194       1   
2621  2020-04-03 22:46:20 -13.133897   27.849332         39       1   
2622  2020-04-03 22:46:20 -19.015438   29.154857          9       1   
2623  2020-04-03 22:46:37        NaN         NaN          0       0   

      Recovered  Active                   Combined_Key  
0             0       0  Abbeville, South Carolina, US  
1             0       0          Acadia, Louisiana, US  
2             0       0         Accomack, Virginia, US  
3             0       0                 Ada, Idaho, US  
4             0       0                Adair, Iowa, US  
...         ...     ...                            ...  
2619         85     152                        Vietnam  
2620         21     172             West Bank and Gaza  
2621          2      36                         Zambia  
2622          0       8                       Zimbabwe  
2623          0       0        unassigned, Wyoming, US  

[2624 rows x 12 columns]

In [3]:
by_country = corona_df.groupby('Country_Region').sum()[['Confirmed', 'Deaths', 'Recovered', 'Active']]
cdf = by_country.nlargest(15, 'Confirmed')[['Confirmed']]
cdf

Confirmed
Country_Region           
US                 275586
Italy              119827
Spain              119199
Germany             91159
China               82511
France              65202
Iran                53183
United Kingdom      38689
Turkey              20921
Switzerland         19606
Belgium             16770
Netherlands         15821
Canada              12437
Austria             11524
Korea, South        10062

In [4]:
!pip install folium

In [5]:
import folium
corona_df=corona_df.dropna()

m=folium.Map(location=[34.223334,-82.461707],
            tiles='Stamen toner',
            zoom_start=8)

def circle_maker(x):
    folium.Circle(location=[x[0],x[1]],
                 radius=float(x[2])*10,
                 color="red",
                 popup='{}\n confirmed cases:{}'.format(x[3],x[2])).add_to(m)
corona_df[['Lat','Long_','Confirmed','Combined_Key']].apply(lambda x:circle_maker(x),axis=1)
m


In [6]:
html_map=m._repr_html_()
html_map

'<div style="width:100%;"><div style="position:relative;width:100%;height:0;padding-bottom:60%;"><span style="color:#565656">Make this Notebook Trusted to load map: File -> Trust Notebook</span><iframe src="about:blank" style="position:absolute;width:100%;height:100%;left:0;top:0;border:none !important;" data-html=%3C%21DOCTYPE%20html%3E%0A%3Chead%3E%20%20%20%20%0A%20%20%20%20%3Cmeta%20http-equiv%3D%22content-type%22%20content%3D%22text/html%3B%20charset%3DUTF-8%22%20/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%3Cscript%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20L_NO_TOUCH%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20L_DISABLE_3D%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%3C/script%3E%0A%20%20%20%20%0A%20%20%20%20%3Cstyle%3Ehtml%2C%20body%20%7Bwidth%3A%20100%25%3Bheight%3A%20100%25%3Bmargin%3A%200%3Bpadding%3A%200%3B%7D%3C/style%3E%0A%20%20%20%20%3Cstyle%3E%23map%20%7Bposition%3Aabsolute%3Btop%3A0%3Bbottom%3A0%3Bright%3A0%3Bleft%3A0%3B%7D%3C/style%3E%0A%20%20%20%20%3Cscript%

In [ ]:
from flask import Flask,render_template

app=Flask(__name__,template_folder='template',static_folder='../static')

@app.route('/')
def home():
    return render_template("home.html",table=cdf, cmap=html_map,pairs=pairs)

if __name__=="__main__":
    app.run()